In [1]:
import os
import struct
import tqdm, tqdm.notebook
tqdm.tqdm = tqdm.notebook.tqdm
from pathlib import Path
import numpy as np
import collections
from hloc import extract_features, match_features, reconstruction,pairs_from_retrieval


import pycolmap
import time
from hloc.localize_sfm import QueryLocalizer, pose_from_cluster
import json


import torch
import torchvision.transforms as transforms
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [2]:
retrieval_conf = extract_features.confs['netvlad']
feature_conf = extract_features.confs['superpoint_aachen']
matcher_conf = match_features.confs['superpoint+lightglue']

# Force GPU usage
retrieval_conf['device'] = 'cuda'  # Ensure NetVLAD uses GPU
feature_conf['device'] = 'cuda'    # Ensure SuperPoint uses GPU
matcher_conf['device'] = 'cuda'    # Ensure LightGlue uses GPU

In [3]:
# Paths
images = Path('/media/siyanhu/T71/hloc/datasets_ref/')
outputs = Path('/media/siyanhu/T71/hloc/ref_recon')

sfm_pairs = outputs / 'pairs-netvlad.txt'
loc_pairs = outputs / 'pairs-loc.txt'

sfm_dir = outputs / 'sfm'
features = outputs / 'features.h5'
matches = outputs / 'matches.h5'
retrieval_features = outputs/'features_retrieval.h5'

In [4]:
ref_seqs = [1, 2, 3, 4, 5, 6]
query_seqs = [7, 8, 9]

ref_paths = []
query_paths = []

for i in range(9):
    seq_num = i + 1
    if seq_num in ref_seqs:
        for p in (images / f'rgb{seq_num}/').iterdir():
            if '.jpg' in str(p.relative_to(images)):
                    ref_paths.append(str(p.relative_to(images)))
    elif seq_num in query_seqs:
        for p in (images / f'rgb{seq_num}/').iterdir():
            if '.jpg' in str(p.relative_to(images)):
                    query_paths.append(str(p.relative_to(images)))
    
print(ref_paths[5:10], ref_paths[-10:-5])
print(query_paths[5:10], query_paths[-10:-5])

['rgb1/00006.jpg', 'rgb1/00007.jpg', 'rgb1/00008.jpg', 'rgb1/00009.jpg', 'rgb1/00010.jpg'] ['rgb6/00746.jpg', 'rgb6/00747.jpg', 'rgb6/00748.jpg', 'rgb6/00749.jpg', 'rgb6/00750.jpg']
['rgb7/00006.jpg', 'rgb7/00007.jpg', 'rgb7/00008.jpg', 'rgb7/00009.jpg', 'rgb7/00010.jpg'] ['rgb9/00747.jpg', 'rgb9/00748.jpg', 'rgb9/00749.jpg', 'rgb9/00750.jpg', 'rgb9/00751.jpg']


In [20]:
def filter_query_images(ref_register_list):
    skip_list = ['rgb7', 'rgb8', 'rgb9']
    ref_register = []
    for name in ref_register_list:
        prefix = name.split('/')[0]
        if prefix not in skip_list:
            ref_register.append(name)
    print(ref_register[5:10], ref_register[-10:-5])
    return ref_register

In [24]:
total_model_num = 5
models = []
ref_registers = {}
for model_index in range(total_model_num):
    model = pycolmap.Reconstruction(sfm_dir/'models'/str(model_index))
    references_registered_init0 = [model.images[i].name for i in model.reg_image_ids()]
    # print(references_registered_init0[5:10], references_registered_init0[-10:-5])
    references_registered_0 = filter_query_images(references_registered_init0)
    models.append(model)
    ref_registers[model_index] = references_registered_0

['rgb1/00006.jpg', 'rgb1/00007.jpg', 'rgb1/00008.jpg', 'rgb1/00009.jpg', 'rgb1/00010.jpg'] ['rgb3/00746.jpg', 'rgb3/00747.jpg', 'rgb3/00748.jpg', 'rgb3/00749.jpg', 'rgb3/00750.jpg']
['rgb4/00006.jpg', 'rgb4/00007.jpg', 'rgb4/00008.jpg', 'rgb4/00009.jpg', 'rgb4/00010.jpg'] ['rgb6/00746.jpg', 'rgb6/00747.jpg', 'rgb6/00748.jpg', 'rgb6/00749.jpg', 'rgb6/00750.jpg']
[] []
[] []
[] []


In [25]:
ret_list = []
log_list = []
pose_dict = {}
time_total = 0

def parse_retrieval(path):
    retrieval = []
    with open(path, "r") as f:
        for p in f.read().rstrip("\n").split("\n"):
            if len(p) == 0:
                continue
            q, r = p.split()
            retrieval.append(r)
    return retrieval

In [30]:
def query_position(query_list, model, references_registered, model_index):
    count = 0
    time_total = 0  # Initialize total time
    output_file_path = '_'.join([str(outputs), str(model_index), '_query_results.json'])
    
    # Open the output file in write mode and initialize it as a JSON array
    with open(output_file_path, 'w') as json_file:
        json_file.write('[\n')  # Begin the JSON array
        
        for query in query_list:
            count += 1
            print('progress: ', count / len(query_list), 'query: ', query)
            time_start = time.time()
            
            # Your existing feature extraction and matching logic
            extract_features.main(feature_conf, images, image_list=[query], feature_path=features, overwrite=True)
            global_descriptors = extract_features.main(retrieval_conf, images, image_list=[query], feature_path=retrieval_features)
            pairs_from_retrieval.main(global_descriptors, loc_pairs, num_matched=20, db_list=references_registered, query_list=[query])
            match_features.main(matcher_conf, loc_pairs, features=features, matches=matches, overwrite=True)
            retrieval_images = parse_retrieval(loc_pairs)
            camera = pycolmap.infer_camera_from_image(images / query)
            
            ref_ids = []
            for n in references_registered:
                if n in retrieval_images:
                    ref_ids.append(model.find_image_with_name(n).image_id)
            print(ref_ids)
            
            conf = {
                'estimation': {'ransac': {'max_error': 12}},
                'refinement': {'refine_focal_length': True, 'refine_extra_params': True},
            }
            localizer = QueryLocalizer(model, conf)
            
            try:
                ret, log = pose_from_cluster(localizer, query, camera, ref_ids, features, matches)
                time_end = time.time()
                inference_time = time_end - time_start
                time_total += inference_time
                
                # Create the result dictionary
                result = {
                    "query": query,
                    "rotation": ret['cam_from_world'].rotation.quat.tolist(),
                    "translation": ret['cam_from_world'].translation.tolist(),
                    "inference_time": inference_time
                }
                
                # Write the result to the file
                json.dump(result, json_file)
                
                # Add a comma if this is not the last query
                if count < len(query_list):
                    json_file.write(',\n')
                else:
                    json_file.write('\n')  # Final entry, no comma
            except Exception as e:
                print("============================================")
                print(e)
                print("============================================")
                pass
        
        json_file.write(']\n')  # End the JSON array
    print('avg inference time: ', time_total / len(query_list))

In [ ]:
# def query_position(query_list, model, references_registered, model_index):
# query_paths

for model_index in range(total_model_num):
    query_position(query_paths, models[model_index], ref_registers[model_index], model_index)

[2025/03/16 14:18:35 hloc INFO] Extracting local features with configuration:
{'device': 'cuda',
 'model': {'max_keypoints': 4096, 'name': 'superpoint', 'nms_radius': 3},
 'output': 'feats-superpoint-n4096-r1024',
 'preprocessing': {'grayscale': True, 'resize_max': 1024}}


progress:  0.0004409171075837742 query:  rgb7/00001.jpg
Loaded SuperPoint model


  0%|          | 0/1 [00:00<?, ?it/s]

[2025/03/16 14:18:36 hloc INFO] Finished exporting features.
[2025/03/16 14:18:36 hloc INFO] Extracting local features with configuration:
{'device': 'cuda',
 'model': {'name': 'netvlad'},
 'output': 'global-feats-netvlad',
 'preprocessing': {'resize_max': 1024}}
[2025/03/16 14:18:36 hloc INFO] Skipping the extraction.
[2025/03/16 14:18:36 hloc INFO] Extracting image pairs from a retrieval database.
[2025/03/16 14:18:38 hloc INFO] Found 20 pairs.
[2025/03/16 14:18:38 hloc INFO] Matching local features with configuration:
{'device': 'cuda',
 'model': {'features': 'superpoint', 'name': 'lightglue'},
 'output': 'matches-superpoint-lightglue'}


  0%|          | 0/20 [00:00<?, ?it/s]

...

[2025/03/16 19:49:59 hloc INFO] Finished exporting features.
[2025/03/16 19:49:59 hloc INFO] Extracting local features with configuration:
{'device': 'cuda',
 'model': {'name': 'netvlad'},
 'output': 'global-feats-netvlad',
 'preprocessing': {'resize_max': 1024}}
[2025/03/16 19:50:00 hloc INFO] Skipping the extraction.
[2025/03/16 19:50:00 hloc INFO] Extracting image pairs from a retrieval database.
[2025/03/16 19:50:02 hloc INFO] Found 20 pairs.
[2025/03/16 19:50:02 hloc INFO] Matching local features with configuration:
{'device': 'cuda',
 'model': {'features': 'superpoint', 'name': 'lightglue'},
 'output': 'matches-superpoint-lightglue'}


  0%|          | 0/20 [00:00<?, ?it/s]

[2025/03/16 19:50:03 hloc INFO] Finished exporting matches.
E20250316 19:50:03.372932 130801370576704 images.cc:72] Check failed: ExistsFile(image_path) File /media/siyanhu/T71/hloc/datasets_ref/rgb7/00273.jpg does not exist.


ValueError: [images.cc:72] Check failed: ExistsFile(image_path) File /media/siyanhu/T71/hloc/datasets_ref/rgb7/00273.jpg does not exist.

: 